In [1]:
from sqlalchemy import create_engine, text
import pandas as pd

# Database connection setup
DATABASE_TYPE = 'mysql'
DBAPI = 'mysqlconnector'
HOST = 'fashionretail.c3q4cw8i0vbc.us-east-2.rds.amazonaws.com'
USER = 'admin'
PASSWORD = 'bsan-6080-project'
DATABASE = 'fashion_retail_sales'
DATABASE_URL = f"{DATABASE_TYPE}+{DBAPI}://{USER}:{PASSWORD}@{HOST}/{DATABASE}"
engine = create_engine(DATABASE_URL, echo=True)

# Load the CSV file
csv_file_path = 'Fashion_Retail_Sales_Clean.csv'
df = pd.read_csv(csv_file_path)

# Convert 'Date Purchase' to datetime and 'Purchase Amount (USD)' to numeric
df['DatePurchased'] = pd.to_datetime(df['Date Purchase'])
df['Revenue'] = pd.to_numeric(df['Purchase Amount (USD)'], errors='coerce')

# Extract date parts
df['Day'] = df['DatePurchased'].dt.day
df['Month'] = df['DatePurchased'].dt.month
df['Quarter'] = df['DatePurchased'].dt.quarter
df['Year'] = df['DatePurchased'].dt.year

# Rename columns to match database schema and include Review Rating
df = df.rename(columns={
    'Customer Reference ID': 'CustomerID',
    'Item Purchased': 'ItemsPurchased',
    'Review Rating': 'ReviewRating'
})

# SQL for creating tables
create_table_statements = [
    """
    CREATE TABLE IF NOT EXISTS fact_purchases (
        PurchaseID INT AUTO_INCREMENT PRIMARY KEY,
        DatePurchased DATE,
        ItemsPurchased VARCHAR(255),
        Revenue DECIMAL(10, 2),
        ReviewRating DECIMAL(3, 1)
    );
    """,
    """
    CREATE TABLE IF NOT EXISTS dim_date (
        DatePurchased DATE PRIMARY KEY,
        Day INT,
        Month INT,
        Quarter INT,
        Year INT
    );
    """,
    """
    CREATE TABLE IF NOT EXISTS fact_customer_purchases (
        CustomerID INT,
        DatePurchased DATE,
        ItemsPurchased VARCHAR(255),
        Revenue DECIMAL(10, 2),
        ReviewRating DECIMAL(3, 1),
        PRIMARY KEY (CustomerID, DatePurchased),
        FOREIGN KEY (DatePurchased) REFERENCES dim_date(DatePurchased)
    );
    """
]

# Insertion queries with ON DUPLICATE KEY UPDATE
queries = {
    'fact_purchases': """
    INSERT INTO fact_purchases (DatePurchased, ItemsPurchased, Revenue, ReviewRating)
    VALUES (:DatePurchased, :ItemsPurchased, :Revenue, :ReviewRating)
    ON DUPLICATE KEY UPDATE
    ItemsPurchased=VALUES(ItemsPurchased), Revenue=VALUES(Revenue), ReviewRating=VALUES(ReviewRating);
    """,
    'dim_date': """
    INSERT INTO dim_date (DatePurchased, Day, Month, Quarter, Year)
    VALUES (:DatePurchased, :Day, :Month, :Quarter, :Year)
    ON DUPLICATE KEY UPDATE
    Day=VALUES(Day), Month=VALUES(Month), Quarter=VALUES(Quarter), Year=VALUES(Year);
    """,
    'fact_customer_purchases': """
    INSERT INTO fact_customer_purchases (CustomerID, DatePurchased, ItemsPurchased, Revenue, ReviewRating)
    VALUES (:CustomerID, :DatePurchased, :ItemsPurchased, :Revenue, :ReviewRating)
    ON DUPLICATE KEY UPDATE
    ItemsPurchased=VALUES(ItemsPurchased), Revenue=VALUES(Revenue), ReviewRating=VALUES(ReviewRating);
    """
}

# Execute the table creation and data insertion within a single transaction
with engine.begin() as conn:
    # Ensure tables exist
    for statement in create_table_statements:
        conn.execute(text(statement))
    
    # Insert data into all tables
    for index, row in df.iterrows():
        row['DatePurchased'] = row['DatePurchased'].date().isoformat()  # Convert to ISO format string
        for table, query in queries.items():
            conn.execute(text(query), row.to_dict())

print("All tables populated successfully.")


2024-04-23 18:43:39,592 INFO sqlalchemy.engine.Engine SELECT DATABASE()
2024-04-23 18:43:39,596 INFO sqlalchemy.engine.Engine [raw sql] {}
2024-04-23 18:43:40,092 INFO sqlalchemy.engine.Engine SELECT @@sql_mode
2024-04-23 18:43:40,094 INFO sqlalchemy.engine.Engine [raw sql] {}
2024-04-23 18:43:40,341 INFO sqlalchemy.engine.Engine SELECT @@lower_case_table_names
2024-04-23 18:43:40,343 INFO sqlalchemy.engine.Engine [raw sql] {}
2024-04-23 18:43:40,510 INFO sqlalchemy.engine.Engine BEGIN (implicit)
2024-04-23 18:43:40,680 INFO sqlalchemy.engine.Engine 
    CREATE TABLE IF NOT EXISTS fact_purchases (
        PurchaseID INT AUTO_INCREMENT PRIMARY KEY,
        DatePurchased DATE,
        ItemsPurchased VARCHAR(255),
        Revenue DECIMAL(10, 2),
        ReviewRating DECIMAL(3, 1)
    );
    
2024-04-23 18:43:40,684 INFO sqlalchemy.engine.Engine [generated in 0.16880s] {}
2024-04-23 18:43:40,977 INFO sqlalchemy.engine.Engine 
    CREATE TABLE IF NOT EXISTS dim_date (
        DatePurchased 

2024-04-23 18:43:44,807 INFO sqlalchemy.engine.Engine [cached since 3.435s ago] {'DatePurchased': '2022-11-27', 'ItemsPurchased': 'Wallet', 'Revenue': 3003.0, 'ReviewRating': 4.7}
2024-04-23 18:43:45,050 INFO sqlalchemy.engine.Engine 
    INSERT INTO dim_date (DatePurchased, Day, Month, Quarter, Year)
    VALUES (%(DatePurchased)s, %(Day)s, %(Month)s, %(Quarter)s, %(Year)s)
    ON DUPLICATE KEY UPDATE
    Day=VALUES(Day), Month=VALUES(Month), Quarter=VALUES(Quarter), Year=VALUES(Year);
    
2024-04-23 18:43:45,052 INFO sqlalchemy.engine.Engine [cached since 3.18s ago] {'DatePurchased': '2022-11-27', 'Day': 27, 'Month': 11, 'Quarter': 4, 'Year': 2022}
2024-04-23 18:43:45,302 INFO sqlalchemy.engine.Engine 
    INSERT INTO fact_customer_purchases (CustomerID, DatePurchased, ItemsPurchased, Revenue, ReviewRating)
    VALUES (%(CustomerID)s, %(DatePurchased)s, %(ItemsPurchased)s, %(Revenue)s, %(ReviewRating)s)
    ON DUPLICATE KEY UPDATE
    ItemsPurchased=VALUES(ItemsPurchased), Revenue=VA

2024-04-23 18:43:48,796 INFO sqlalchemy.engine.Engine 
    INSERT INTO dim_date (DatePurchased, Day, Month, Quarter, Year)
    VALUES (%(DatePurchased)s, %(Day)s, %(Month)s, %(Quarter)s, %(Year)s)
    ON DUPLICATE KEY UPDATE
    Day=VALUES(Day), Month=VALUES(Month), Quarter=VALUES(Quarter), Year=VALUES(Year);
    
2024-04-23 18:43:48,797 INFO sqlalchemy.engine.Engine [cached since 6.925s ago] {'DatePurchased': '2023-06-11', 'Day': 11, 'Month': 6, 'Quarter': 2, 'Year': 2023}
2024-04-23 18:43:49,045 INFO sqlalchemy.engine.Engine 
    INSERT INTO fact_customer_purchases (CustomerID, DatePurchased, ItemsPurchased, Revenue, ReviewRating)
    VALUES (%(CustomerID)s, %(DatePurchased)s, %(ItemsPurchased)s, %(Revenue)s, %(ReviewRating)s)
    ON DUPLICATE KEY UPDATE
    ItemsPurchased=VALUES(ItemsPurchased), Revenue=VALUES(Revenue), ReviewRating=VALUES(ReviewRating);
    
2024-04-23 18:43:49,047 INFO sqlalchemy.engine.Engine [cached since 6.927s ago] {'CustomerID': 4010, 'DatePurchased': '2023-0

2024-04-23 18:43:52,550 INFO sqlalchemy.engine.Engine [cached since 10.68s ago] {'DatePurchased': '2023-08-01', 'Day': 1, 'Month': 8, 'Quarter': 3, 'Year': 2023}
2024-04-23 18:43:52,799 INFO sqlalchemy.engine.Engine 
    INSERT INTO fact_customer_purchases (CustomerID, DatePurchased, ItemsPurchased, Revenue, ReviewRating)
    VALUES (%(CustomerID)s, %(DatePurchased)s, %(ItemsPurchased)s, %(Revenue)s, %(ReviewRating)s)
    ON DUPLICATE KEY UPDATE
    ItemsPurchased=VALUES(ItemsPurchased), Revenue=VALUES(Revenue), ReviewRating=VALUES(ReviewRating);
    
2024-04-23 18:43:52,802 INFO sqlalchemy.engine.Engine [cached since 10.68s ago] {'CustomerID': 4044, 'DatePurchased': '2023-08-01', 'ItemsPurchased': 'Handbag', 'Revenue': 2122.0, 'ReviewRating': 1.2}
2024-04-23 18:43:53,049 INFO sqlalchemy.engine.Engine 
    INSERT INTO fact_purchases (DatePurchased, ItemsPurchased, Revenue, ReviewRating)
    VALUES (%(DatePurchased)s, %(ItemsPurchased)s, %(Revenue)s, %(ReviewRating)s)
    ON DUPLICATE K

2024-04-23 18:43:56,501 INFO sqlalchemy.engine.Engine 
    INSERT INTO fact_customer_purchases (CustomerID, DatePurchased, ItemsPurchased, Revenue, ReviewRating)
    VALUES (%(CustomerID)s, %(DatePurchased)s, %(ItemsPurchased)s, %(Revenue)s, %(ReviewRating)s)
    ON DUPLICATE KEY UPDATE
    ItemsPurchased=VALUES(ItemsPurchased), Revenue=VALUES(Revenue), ReviewRating=VALUES(ReviewRating);
    
2024-04-23 18:43:56,503 INFO sqlalchemy.engine.Engine [cached since 14.38s ago] {'CustomerID': 4103, 'DatePurchased': '2022-11-21', 'ItemsPurchased': 'Romper', 'Revenue': 4465.0, 'ReviewRating': 3.4}
2024-04-23 18:43:56,758 INFO sqlalchemy.engine.Engine 
    INSERT INTO fact_purchases (DatePurchased, ItemsPurchased, Revenue, ReviewRating)
    VALUES (%(DatePurchased)s, %(ItemsPurchased)s, %(Revenue)s, %(ReviewRating)s)
    ON DUPLICATE KEY UPDATE
    ItemsPurchased=VALUES(ItemsPurchased), Revenue=VALUES(Revenue), ReviewRating=VALUES(ReviewRating);
    
2024-04-23 18:43:56,760 INFO sqlalchemy.engin

...

2024-04-23 19:26:42,876 INFO sqlalchemy.engine.Engine 
    INSERT INTO fact_purchases (DatePurchased, ItemsPurchased, Revenue, ReviewRating)
    VALUES (%(DatePurchased)s, %(ItemsPurchased)s, %(Revenue)s, %(ReviewRating)s)
    ON DUPLICATE KEY UPDATE
    ItemsPurchased=VALUES(ItemsPurchased), Revenue=VALUES(Revenue), ReviewRating=VALUES(ReviewRating);
    
2024-04-23 19:26:42,877 INFO sqlalchemy.engine.Engine [cached since 2582s ago] {'DatePurchased': '2023-03-22', 'ItemsPurchased': 'Raincoat', 'Revenue': 126.0, 'ReviewRating': 1.7}
2024-04-23 19:26:43,136 INFO sqlalchemy.engine.Engine 
    INSERT INTO dim_date (DatePurchased, Day, Month, Quarter, Year)
    VALUES (%(DatePurchased)s, %(Day)s, %(Month)s, %(Quarter)s, %(Year)s)
    ON DUPLICATE KEY UPDATE
    Day=VALUES(Day), Month=VALUES(Month), Quarter=VALUES(Quarter), Year=VALUES(Year);
    
2024-04-23 19:26:43,138 INFO sqlalchemy.engine.Engine [cached since 2581s ago] {'DatePurchased': '2023-03-22', 'Day': 22, 'Month': 3, 'Quarter': 

2024-04-23 19:26:46,660 INFO sqlalchemy.engine.Engine [cached since 2585s ago] {'DatePurchased': '2023-01-03', 'ItemsPurchased': 'Polo Shirt', 'Revenue': 76.0, 'ReviewRating': 2.9}
2024-04-23 19:26:46,899 INFO sqlalchemy.engine.Engine 
    INSERT INTO dim_date (DatePurchased, Day, Month, Quarter, Year)
    VALUES (%(DatePurchased)s, %(Day)s, %(Month)s, %(Quarter)s, %(Year)s)
    ON DUPLICATE KEY UPDATE
    Day=VALUES(Day), Month=VALUES(Month), Quarter=VALUES(Quarter), Year=VALUES(Year);
    
2024-04-23 19:26:46,901 INFO sqlalchemy.engine.Engine [cached since 2585s ago] {'DatePurchased': '2023-01-03', 'Day': 3, 'Month': 1, 'Quarter': 1, 'Year': 2023}
2024-04-23 19:26:47,145 INFO sqlalchemy.engine.Engine 
    INSERT INTO fact_customer_purchases (CustomerID, DatePurchased, ItemsPurchased, Revenue, ReviewRating)
    VALUES (%(CustomerID)s, %(DatePurchased)s, %(ItemsPurchased)s, %(Revenue)s, %(ReviewRating)s)
    ON DUPLICATE KEY UPDATE
    ItemsPurchased=VALUES(ItemsPurchased), Revenue=VAL

2024-04-23 19:26:50,669 INFO sqlalchemy.engine.Engine 
    INSERT INTO dim_date (DatePurchased, Day, Month, Quarter, Year)
    VALUES (%(DatePurchased)s, %(Day)s, %(Month)s, %(Quarter)s, %(Year)s)
    ON DUPLICATE KEY UPDATE
    Day=VALUES(Day), Month=VALUES(Month), Quarter=VALUES(Quarter), Year=VALUES(Year);
    
2024-04-23 19:26:50,670 INFO sqlalchemy.engine.Engine [cached since 2589s ago] {'DatePurchased': '2023-02-13', 'Day': 13, 'Month': 2, 'Quarter': 1, 'Year': 2023}
2024-04-23 19:26:50,922 INFO sqlalchemy.engine.Engine 
    INSERT INTO fact_customer_purchases (CustomerID, DatePurchased, ItemsPurchased, Revenue, ReviewRating)
    VALUES (%(CustomerID)s, %(DatePurchased)s, %(ItemsPurchased)s, %(Revenue)s, %(ReviewRating)s)
    ON DUPLICATE KEY UPDATE
    ItemsPurchased=VALUES(ItemsPurchased), Revenue=VALUES(Revenue), ReviewRating=VALUES(ReviewRating);
    
2024-04-23 19:26:50,924 INFO sqlalchemy.engine.Engine [cached since 2589s ago] {'CustomerID': 4094, 'DatePurchased': '2023-02-

2024-04-23 19:26:54,546 INFO sqlalchemy.engine.Engine [cached since 2593s ago] {'DatePurchased': '2022-10-15', 'Day': 15, 'Month': 10, 'Quarter': 4, 'Year': 2022}
2024-04-23 19:26:54,816 INFO sqlalchemy.engine.Engine 
    INSERT INTO fact_customer_purchases (CustomerID, DatePurchased, ItemsPurchased, Revenue, ReviewRating)
    VALUES (%(CustomerID)s, %(DatePurchased)s, %(ItemsPurchased)s, %(Revenue)s, %(ReviewRating)s)
    ON DUPLICATE KEY UPDATE
    ItemsPurchased=VALUES(ItemsPurchased), Revenue=VALUES(Revenue), ReviewRating=VALUES(ReviewRating);
    
2024-04-23 19:26:54,818 INFO sqlalchemy.engine.Engine [cached since 2593s ago] {'CustomerID': 4110, 'DatePurchased': '2022-10-15', 'ItemsPurchased': 'Polo Shirt', 'Revenue': 42.0, 'ReviewRating': 4.0}
2024-04-23 19:26:55,057 INFO sqlalchemy.engine.Engine 
    INSERT INTO fact_purchases (DatePurchased, ItemsPurchased, Revenue, ReviewRating)
    VALUES (%(DatePurchased)s, %(ItemsPurchased)s, %(Revenue)s, %(ReviewRating)s)
    ON DUPLICATE 

2024-04-23 19:26:58,608 INFO sqlalchemy.engine.Engine 
    INSERT INTO fact_customer_purchases (CustomerID, DatePurchased, ItemsPurchased, Revenue, ReviewRating)
    VALUES (%(CustomerID)s, %(DatePurchased)s, %(ItemsPurchased)s, %(Revenue)s, %(ReviewRating)s)
    ON DUPLICATE KEY UPDATE
    ItemsPurchased=VALUES(ItemsPurchased), Revenue=VALUES(Revenue), ReviewRating=VALUES(ReviewRating);
    
2024-04-23 19:26:58,610 INFO sqlalchemy.engine.Engine [cached since 2597s ago] {'CustomerID': 4042, 'DatePurchased': '2023-01-01', 'ItemsPurchased': 'Sandals', 'Revenue': 128.0, 'ReviewRating': 1.8}
2024-04-23 19:26:58,857 INFO sqlalchemy.engine.Engine 
    INSERT INTO fact_purchases (DatePurchased, ItemsPurchased, Revenue, ReviewRating)
    VALUES (%(DatePurchased)s, %(ItemsPurchased)s, %(Revenue)s, %(ReviewRating)s)
    ON DUPLICATE KEY UPDATE
    ItemsPurchased=VALUES(ItemsPurchased), Revenue=VALUES(Revenue), ReviewRating=VALUES(ReviewRating);
    
2024-04-23 19:26:58,859 INFO sqlalchemy.engine